In [2]:
import pandas as pd

query = """
    select  final.CUSTOMER_NUMBER_main as Focal_id,
            final.Credit_transaction_amount,
            final.Total_no_of_credit_transactions,
            final.Debit_transaction_amount,
            final.Total_no_of_debit_transactions,
            final.SEGMENT,
            final.RISK,
            final.SAR_FLAG
    from 
    (
        (
            select subquery.CUSTOMER_NUMBER_1 as CUSTOMER_NUMBER_main,
                    subquery.Credit_transaction_amount,
                    subquery.Total_no_of_credit_transactions,
                    case
                         when subquery.Debit_transaction_amount is NULL then 0
                         else Debit_transaction_amount
                    end as Debit_transaction_amount,
                    case
                         when subquery.Total_no_of_debit_transactions is NULL then 0
                         else Total_no_of_debit_transactions
                    end as Total_no_of_debit_transactions
            from 
            (
                (
                    select customer_number as CUSTOMER_NUMBER_1, 
                            sum(transaction_amount) as Credit_transaction_amount, 
                            count(*) as Total_no_of_credit_transactions
                    from 
                    (
                        select * 
                        from {trans_data} trans_table left join {acc_data} acc_table
                        on trans_table.benef_account_number = acc_table.account_number
                    )
                    where account_number not in ('None')
                    group by 1
                ) credit left join
                (
                    select customer_number as CUSTOMER_NUMBER_2, 
                            sum(transaction_amount) as Debit_transaction_amount, 
                            count(*) as Total_no_of_debit_transactions
                    from 
                    (
                        select * 
                        from {trans_data} trans_table left join {acc_data} acc_table
                        on trans_table.orig_account_number = acc_table.account_number
                    )
                    where account_number not in ('None')
                    group by 1
                ) debit on credit.CUSTOMER_NUMBER_1 = debit.CUSTOMER_NUMBER_2 
            ) subquery
        ) main left join 
        (
            select subquery.CUSTOMER_NUMBER_3 as CUSTOMER_NUMBER_cust,
                    subquery.SEGMENT,
                    subquery.RISK,
                    case
                         when subquery.SAR_FLAG is NULL then 'N'
                         else subquery.SAR_FLAG
                    end as SAR_FLAG    
            from
            (
                (
                    select customer_number as CUSTOMER_NUMBER_3, 
                            business_segment as SEGMENT,
                            case
                                when RISK_CLASSIFICATION = 1 then 'Low Risk'
                                when RISK_CLASSIFICATION = 2 then 'Medium Risk'
                                when RISK_CLASSIFICATION = 3 then 'High Risk'
                                else 'Unknown Risk'
                            end AS RISK
                    from {cust_data}
                ) cd left join
                (
                    select customer_number as CUSTOMER_NUMBER_4, 
                            sar_flag as SAR_FLAG
                    from {alert_data}
                ) ad on cd.CUSTOMER_NUMBER_3 = ad.CUSTOMER_NUMBER_4
            ) subquery
        ) cust_alert on cust_alert.CUSTOMER_NUMBER_cust = main.CUSTOMER_NUMBER_main
    ) final
"""

from tms_data_interface import SQLQueryInterface
 
class Scenario:
    seq = SQLQueryInterface(schema="transactionschema")
 
    def logic(self, **kwargs):
        row_list = self.seq.execute_raw(query.format(trans_data="transaction10m",
                                                    cust_data="customer_data_v1",
                                                    acc_data="account_data_v1",
                                                    alert_data="alert_data_v1")
                                       )
        cols = ["Focal_id", "Credit_transaction_amount", "Total_no_of_credit_transactions",
                "Debit_transaction_amount", "Total_no_of_debit_transactions",
                "Segment", "Risk", "SAR_FLAG"]
        df = pd.DataFrame(row_list, columns = cols)
        return df

In [3]:
# sen = Scenario()
# sen.logic()

Focal_id  Credit_transaction_amount  Total_no_of_credit_transactions  \
0      PN182121               1.644268e+09                             1168   
1      PN476208               2.792031e+09                             1993   
2      PN413985               3.621153e+09                             2438   
3      PN906130               1.666937e+09                             1222   
4      PN446914               3.379522e+09                             2378   
...         ...                        ...                              ...   
10009  PN723207               4.765892e+07                              298   
10010  PN860773               3.537672e+07                              256   
10011  PN741843               3.787797e+07                              255   
10012  PN588393               3.567320e+07                              254   
10013  PN168372               3.166679e+07                              253   

       Debit_transaction_amount  Total_no_of_debit_transactions  \
0                  1.717572e+09                            1198   
1                  2.777591e+09                            2010   
2                  3.290559e+09                            2375   
3                  1.756952e+09                            1177   
4                  3.512353e+09                            2454   
...                         ...                             ...   
10009              2.651826e+07                             378   
10010              2.578618e+07                             363   
10011              2.909541e+07                             346   
10012              2.676294e+07                             391   
10013              2.707380e+07                             355   

                   Segment         Risk SAR_FLAG  
0                      SME     Low Risk        N  
1       Whole Sale Banking     Low Risk        N  
2                      SME    High Risk        N  
3       Whole Sale Banking     Low Risk        N  
4                      SME     Low Risk        N  
...                    ...          ...      ...  
10009  Ultra High NetWorth     Low Risk        N  
10010               Others     Low Risk        N  
10011     Priority Banking  Medium Risk        N  
10012          Mass Market     Low Risk        N  
10013          Mass Market     Low Risk        N  

[10014 rows x 8 columns]